# Title

## subTitle

[link](https://www.google.com)

**bold** *italic* `code`

```python
print('Hello world')
```

```bash

ç

In [10]:
from pathlib import Path
import os
import hjson
import numpy as np
import pandas as pd
from IPython.display import display
from loguru import logger
import time

# Visualization
from phd_visualizations.test_timeseries import experimental_results_plot
from phd_visualizations import save_figure
from phd_visualizations.constants import generate_plotly_config

# Setup environment for running MATLAB code if not done externally
# os.environ["MR"] = f"{os.environ['HOME']}/PSA/MATLAB_runtime/R2023b"
os.environ["MR"] = f"{os.environ['HOME']}/MATLAB/R2023b"
MR = os.environ["MR"]
os.environ["LD_LIBRARY_PATH"] = f"{MR}/runtime/glnxa64:{MR}/bin/glnxa64:{MR}/sys/os/glnxa64:{MR}/sys/opengl/lib/glnxa64"

# auto reload modules
%load_ext autoreload

# Paths definition
src_path = Path(f'{os.getenv("HOME")}/Nextcloud/Juanmi_MED_PSA/EURECAT/')
results_path: Path = src_path / 'results'
data_path: Path = src_path / 'data'
output_path: Path = Path(f'{os.getenv("HOME")}/development_psa/models_psa/docs/attachments')

# filename_opt_result = '20240108_optimization_results.json'
# Debería ser un .csv al que se le hayan añadido las variables faltantes desde librescada:
# - J de variadores y medidor de potencia
# - FT-DES-002_VFD

filename_process_data = '20231030_solarMED.csv'
# filename_process_data = '20230505_solarMED.csv'

filename_process_data2 = '20231030_MED.csv'

# Resample figures using plotly_resampler
resample_figures = False

sample_rate = '60s'
sample_rate_numeric = int(sample_rate[:-1])

# Parameters
cost_w: float = 3 # €/m³, cost of water
cost_e: float = 0.05 # €/kWh, cost of electricity

# initial_datetime = '2024-01-08 10:55'
# final_datetime = '2024-01-08 14:00'

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Pre-processing

In [11]:
from models_psa.utils import data_preprocessing, data_conditioning

data_paths = [data_path / filename_process_data, data_path / filename_process_data2]

with open( Path("data") / "variables_config.hjson") as f:
    vars_config = hjson.load(f)
    

# Load data and preprocess data
df = data_preprocessing(data_paths, vars_config, sample_rate_key=sample_rate)

# Condition data
df = data_conditioning(df, cost_w=cost_w, cost_e=cost_e, sample_rate_numeric=sample_rate_numeric)

2024-04-03 16:19:44.100 | DEBUG    | models_psa.utils:process_dataframe:67 - Index([], dtype='object')
2024-04-03 16:19:44.116 | DEBUG    | models_psa.utils:process_dataframe:67 - Index([], dtype='object')
2024-04-03 16:19:44.134 | WARNING  | phd_visualizations.utils:rename_signal_ids_to_var_ids:55 - Signal id FT-SF-003 not found in dataframe columns.
2024-04-03 16:19:44.138 | WARNING  | phd_visualizations.utils:rename_signal_ids_to_var_ids:55 - Signal id FT-SF-005 not found in dataframe columns.
2024-04-03 16:19:44.139 | WARNING  | phd_visualizations.utils:rename_signal_ids_to_var_ids:55 - Signal id FT-SF-006 not found in dataframe columns.
2024-04-03 16:19:44.139 | WARNING  | phd_visualizations.utils:rename_signal_ids_to_var_ids:55 - Signal id FT-SF-007 not found in dataframe columns.
2024-04-03 16:19:44.147 | WARNING  | phd_visualizations.utils:rename_signal_ids_to_var_ids:55 - Signal id FT-SF-008 not found in dataframe columns.
2024-04-03 16:19:44.148 | WARNING  | phd_visualization

## Visualize test data

In [8]:
# Update plot config
with open( Path("data") / "plot_config.hjson") as f:
    plt_config = hjson.load(f)

fig = experimental_results_plot(plt_config, df, vars_config=vars_config, resample=resample_figures)

fig.show(
    config=generate_plotly_config(fig, figure_name=f'solar_med_{df.index[0].strftime("%Y%m%d")}')
)

NameError: name 'df' is not defined

In [4]:
df.to_csv('data/dev.csv')

NameError: name 'df' is not defined

In [5]:
# Test model
from models_psa.solar_med import SolarMED

%autoreload 2

idx_start = 20
span = 12
idx_end = len(df)
df_mod = pd.DataFrame()

# Initialize model
model = SolarMED(
    sample_time=sample_rate_numeric,
    curve_fits_path='data/curve_fits.json',
    resolution_mode='simple',
    
    # Initial states
    ## Thermal storage
    Tts_h=[df['Tts_h_t'].iloc[idx_start], df['Tts_h_m'].iloc[idx_start], df['Tts_h_b'].iloc[idx_start]], 
    Tts_c=[df['Tts_c_t'].iloc[idx_start], df['Tts_c_m'].iloc[idx_start], df['Tts_c_b'].iloc[idx_start]],
    
    ## Solar field
    Tsf_in_ant=df['Tsf_in'].iloc[idx_start-span:idx_start].values,
    msf_ant=df['qsf'].iloc[idx_start-span:idx_start].values,
    
    cost_w = 3, # €/m³ 
    cost_e = 0.05 # €/kWhe
)

# Run model
# %autoreload 2

for idx in range(idx_start, idx_end):
    # idx = 1
    ds = df.iloc[idx]
    
    logger.info(f"Iteration {idx} / {idx_end}")
    start_time = time.time()
        
    model.step(
        # Decision variables
        ## MED
        mmed_s=ds['qmed_s'],
        mmed_f=ds['qmed_f'],
        Tmed_s_in=ds['Tmed_s_in'],
        Tmed_c_out=ds['Tmed_c_out'],
        ## Thermal storage
        mts_src=ds['qhx_s'],
        ## Solar field
        Tsf_out=ds['Tsf_out'],
        
        # Inputs
        # When the solar field is starting up, a flow can be provided to sync the model with the real system, if a valid Tsf_out is provided, it will be prioritized
        msf=ds['qsf'] if ds['qsf'] > 4 else None,
        
        # Environment variables
        Tmed_c_in=ds['Tmed_c_in'],
        Tamb=ds['Tamb'],
        I=ds['I'],
    )
    
    logger.info(f"Finished Iteration {idx} / {idx_end}, elapsed time: {time.time()-start_time:.2f} seconds. Current operation state is {model.operating_state.name}")

    df_mod = model.to_dataframe(df_mod, rename_flows=True)
    

NameError: name 'df' is not defined

In [9]:
# Sync model index with measured data
df_mod.index = df.index[idx_start:idx if idx<idx_end-1 else idx_end]

# Update plot config
with open( Path("data") / "plot_config_validation.hjson") as f:
    plt_config = hjson.load(f)

fig = experimental_results_plot(plt_config, df, df_comp=df_mod, vars_config=vars_config, resample=resample_figures)

fig.show(
    config=generate_plotly_config(fig, figure_name=f'solar_med_{df.index[0].strftime("%Y%m%d")}')
)

2024-03-19 09:45:27.282 | INFO     | phd_visualizations.test_timeseries:experimental_results_plot:378 - Optimization updates not shown in plot, show_optimization_updates: false
2024-03-19 09:45:27.285 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tamb
2024-03-19 09:45:27.287 | DEBUG    | phd_visualizations.test_timeseries:add_trace:75 - legend_id: global_legend, legend: legend for trace T<sub>amb</sub>
2024-03-19 09:45:27.289 | WARNING  | phd_visualizations.test_timeseries:add_trace:136 - Index of comparison dataframe 0 is not the same as the main dataframe, filling difference with NaNs
2024-03-19 09:45:27.314 | INFO     | phd_visualizations.test_timeseries:add_trace:288 - Trace T<sub>amb</sub> added in yaxis1 (left), row 1, uncertainty: False, comparison: True
2024-03-19 09:45:27.317 | DEBUG    | phd_visualizations.test_timeseries:add_trace:38 - Attempting to add Tmed_c_in
2024-03-19 09:45:27.319 | DEBUG    | phd_visualizations.test_timeseries:add_tr

In [7]:
# Save figure
save_figure(
    figure_name=f"SolarMED_validation_{df.index[0].strftime('%Y%m%d')}", 
    figure_path=output_path,
    fig=fig, formats=('png', 'html'), 
    width=fig.layout.width, height=fig.layout.height, scale=2
)

2024-03-06 16:55:11.072 | INFO     | phd_visualizations:save_figure:33 - Figure saved in [PosixPath('/home/jmserrano/development_psa/models_psa/docs/attachments')]/SolarMED_validation_20231030.png
2024-03-06 16:55:11.418 | INFO     | phd_visualizations:save_figure:33 - Figure saved in [PosixPath('/home/jmserrano/development_psa/models_psa/docs/attachments')]/SolarMED_validation_20231030.html
